# app

> Gradio app.py

In [ ]:
#| default_exp app

In [ ]:
#| hide
from nbdev.showdoc import *

In [ ]:
#| export
import copy
import os

import gradio as gr
from fastcore.utils import in_jupyter
from langchain import LLMChain, OpenAI, PromptTemplate
from langchain.agents import (
    AgentExecutor,
    AgentType,
    OpenAIFunctionsAgent,
    Tool,
    initialize_agent,
    load_tools,
)
from langchain.chains import ConversationChain
from langchain.chat_models import ChatOpenAI
from langchain.memory import ChatMessageHistory, ConversationBufferMemory
from langchain.prompts.chat import (
    ChatPromptTemplate,
    HumanMessagePromptTemplate,
    MessagesPlaceholder,
)
from PIL import Image

import constants
from lv_recipe_chatbot.engineer_prompt import INIT_PROMPT
from lv_recipe_chatbot.ingredient_vision import (
    SAMPLE_IMG_DIR,
    BlipImageCaptioning,
    VeganIngredientFinder,
    format_image,
)
from lv_recipe_chatbot.vegan_recipe_tools import vegan_recipe_edamam_search

In [ ]:
from dotenv import load_dotenv

In [ ]:
#: eval: false
load_dotenv()

True

## Put the chat backend pieces together

In [ ]:
show_doc(ConversationBufferMemory)

---

### ConversationBufferMemory

>      ConversationBufferMemory
>                                (chat_memory:langchain.schema.memory.BaseChatMe
>                                ssageHistory=None,
>                                output_key:Optional[str]=None,
>                                input_key:Optional[str]=None,
>                                return_messages:bool=False,
>                                human_prefix:str='Human', ai_prefix:str='AI',
>                                memory_key:str='history')

Buffer for storing conversation memory.

In [ ]:
show_doc(ChatMessageHistory)

---

### ChatMessageHistory

>      ChatMessageHistory
>                          (messages:List[langchain.schema.messages.BaseMessage]
>                          =[])

In memory implementation of chat message history.

Stores messages in an in memory list.

In [ ]:
show_doc(ChatOpenAI)

---

### ChatOpenAI

>      ChatOpenAI (cache:Optional[bool]=None, verbose:bool=None, callbacks:Union
>                  [List[langchain.callbacks.base.BaseCallbackHandler],langchain
>                  .callbacks.base.BaseCallbackManager,NoneType]=None, callback_
>                  manager:Optional[langchain.callbacks.base.BaseCallbackManager
>                  ]=None, tags:Optional[List[str]]=None,
>                  metadata:Optional[Dict[str,Any]]=None, client:Any=None,
>                  model:str='gpt-3.5-turbo', temperature:float=0.7,
>                  model_kwargs:Dict[str,Any]=None,
>                  openai_api_key:Optional[str]=None,
>                  openai_api_base:Optional[str]=None,
>                  openai_organization:Optional[str]=None,
>                  openai_proxy:Optional[str]=None, request_timeout:Union[float,
>                  Tuple[float,float],NoneType]=None, max_retries:int=6,
>                  streaming:bool=False, n:int=1, max_tokens:Optional[int]=None,
>                  tiktoken_model_name:Optional[str]=None)

Wrapper around OpenAI Chat large language models.

To use, you should have the ``openai`` python package installed, and the
environment variable ``OPENAI_API_KEY`` set with your API key.

Any parameters that are valid to be passed to the openai.create call can be passed
in, even if not explicitly saved on this class.

Example:
    .. code-block:: python

        from langchain.chat_models import ChatOpenAI
        openai = ChatOpenAI(model_name="gpt-3.5-turbo")

In [ ]:
#| eval: false
llm = ChatOpenAI(temperature=1)
MEMORY_KEY = "chat_history"
chat_msgs = INIT_PROMPT.format_prompt(
    ingredients="tofu, brocolli",
    allergies="",
    recipe_freeform_input="The preparation time should be less than 30 minutes. I really love Thai food!",
)
chat_msgs = chat_msgs.to_messages()
results = llm.generate([chat_msgs])

chat_msgs.append(results.generations[0][0].message)
tools = [vegan_recipe_edamam_search]
prompt = OpenAIFunctionsAgent.create_prompt(
    system_message=INIT_PROMPT.messages[0],
    extra_prompt_messages=chat_msgs + [MessagesPlaceholder(variable_name=MEMORY_KEY)],
)
memory = ConversationBufferMemory(
    chat_memory=ChatMessageHistory(messages=chat_msgs),
    return_messages=True,
    memory_key=MEMORY_KEY,
)
agent_executor = AgentExecutor(
    agent=OpenAIFunctionsAgent(llm=llm, tools=tools, prompt=prompt),
    tools=tools,
    memory=memory,
    verbose=True,
)

In [ ]:
# Fails for a weird query
# "tofu, pickles, mustard, olives, tomatoes, lettuce, bell peppers, carrots, bread"

In [ ]:
#| eval: false
memory.chat_memory.messages

[SystemMessage(content="The following is a conversation between a human and a friendly AI chef. \nThe AI is compassionate to animals.\nThe AI generates a simple concise keyword query for a vegan recipe, based on the ingredients, allergies, and other preferences the human has, to use in recipe APIs.\nKnowledge: A vegan diet implies a plant-based diet avoiding all animal foods such as meat (including fish, shellfish and insects), dairy, eggs and honey.\n\nLet's think step by step.\nIf the human messages are unrelated to vegan recipes, remind them of your purpose to recipes.\nOnly generate keyword queries as other tools should be used to fetch full recipes.", additional_kwargs={}),
 AIMessage(content='What ingredients do you wish to cook with?', additional_kwargs={}, example=False),
 HumanMessage(content='Ingredients: tofu, brocolli', additional_kwargs={}, example=False),
 AIMessage(content='Do you have any allergies I should be aware of?', additional_kwargs={}, example=False),
 HumanMess

In [ ]:
#| eval: false
agent_executor.run("Search for vegan recipe")



> Entering new AgentExecutor chain...

Invoking: `vegan_recipe_edamam_search` with `{'query': 'vegan tofu broccoli'}`


[{'label': 'Vegan BBQ teriyaki tofu', 'url': 'https://www.bbcgoodfood.com/recipes/teriyaki-tofu-vegan-barbecue', 'ingredientLines': ['4 tbsp low-salt soy sauce', '2 tbsp soft brown sugar', 'pinch ground ginger', '2 tbsp mirin', '3 tsp sesame oil', '350g block very firm tofu (see tip below) cut into thick slices', '½ tbsp rapeseed oil', '2 courgettes, sliced horizontally into strips', '200g Tenderstem broccoli', 'black and white sesame seeds, to serve'], 'totalTime': 25.0}, {'label': 'Vegan Crispy Stir-Fried Tofu With Broccoli Recipe', 'url': 'http://www.seriouseats.com/recipes/2014/02/vegan-experience-crispy-tofu-broccoli-stir-fry.html', 'ingredientLines': ['1 1/2 quarts vegetable or peanut oil', '1/2 cup plus 2 teaspoons cornstarch, divided', '1/2 cup all-purpose flour', '1/2 teaspoon baking powder', 'Kosher salt', '1/2 cup cold water', '1/2 cup vodka', '1 pound ex

In [ ]:
# | export


class ConversationBot:
    def __init__(self, verbose=True):
        self.chat = ChatOpenAI(temperature=1, verbose=True)
        self.memory = ConversationBufferMemory(return_messages=True)
        self.init_prompt = copy.deepcopy(INIT_PROMPT)
        init_prompt_msgs = self.init_prompt.messages
        self.ai_prompt_questions = {
            "ingredients": init_prompt_msgs[1],
            "allergies": init_prompt_msgs[3],
            "recipe_open_params": init_prompt_msgs[5],
        }
        self.img_cap = BlipImageCaptioning("cpu")
        self.vegan_ingred_finder = VeganIngredientFinder()
        self.verbose = verbose

    def respond(self, user_msg, chat_history):
        response = self._get_bot_response(user_msg, chat_history)
        chat_history.append((user_msg, response))
        return "", chat_history

    def init_conversation(self, formatted_chat_prompt):
        self.conversation = ConversationChain(
            llm=self.chat,
            memory=self.memory,
            prompt=formatted_chat_prompt,
            verbose=self.verbose,
        )

    def reset(self):
        self.memory.clear()
        self.init_prompt = copy.deepcopy(INIT_PROMPT)

    def run_img(self, image: str):
        desc = self.img_cap.inference(format_image(image))
        answer = self.vegan_ingred_finder.list_ingredients(image)
        msg = f"""I uploaded an image that may contain vegan ingredients.
The description of the image is: `{desc}`.
The extracted ingredients are:
```
{answer}
```
"""
        base_prompt = INIT_PROMPT.messages[2].prompt.template
        new_prompt = f"{msg}I may type some more ingredients below.\n{base_prompt}"
        self.init_prompt.messages[2].prompt.template = new_prompt
        return msg

    def _get_bot_response(self, user_msg: str, chat_history) -> str:
        if len(chat_history) < 2:
            return self.ai_prompt_questions["allergies"].prompt.template

        if len(chat_history) < 3:
            return self.ai_prompt_questions["recipe_open_params"].prompt.template

        if len(chat_history) < 4:
            user = 0
            ai = 1
            user_msgs = [msg_pair[user] for msg_pair in chat_history[1:]]
            f_init_prompt = self.init_prompt.format_prompt(
                ingredients=user_msgs[0],
                allergies=user_msgs[1],
                recipe_freeform_input=user_msg,
            )
            chat_msgs = f_init_prompt.to_messages()
            results = self.chat.generate([chat_msgs])
            chat_msgs.extend(
                [
                    results.generations[0][0].message,
                    MessagesPlaceholder(variable_name="history"),
                    HumanMessagePromptTemplate.from_template("{input}"),
                ]
            )
            open_prompt = ChatPromptTemplate.from_messages(chat_msgs)
            # prepare the open conversation chain from this point
            self.init_conversation(open_prompt)
            return results.generations[0][0].message.content

        response = self.conversation.predict(input=user_msg)
        return response

    def __del__(self):
        del self.vegan_ingred_finder

In [ ]:
os.listdir(SAMPLE_IMG_DIR)
SAMPLE_IMG_DIR

Path('/home/evylz/AnimalEquality/lv-recipe-chatbot/assets/images/vegan_ingredients')

In [ ]:
#| eval: false
%time bot = ConversationBot()

CPU times: user 6.19 s, sys: 1.47 s, total: 7.66 s
Wall time: 4.68 s


In [ ]:
#| eval: false
%time print(bot.run_img(SAMPLE_IMG_DIR / "veggie-fridge.jpeg"))

I uploaded an image that may contain vegan ingredients.
The description of the image is: `a refrigerator with food inside`.
The extracted ingredients are:
```
cabbage lettuce onion
apples
rice
plant-based milk
```

CPU times: user 56.7 s, sys: 63.6 ms, total: 56.8 s
Wall time: 5.95 s


In [ ]:
#| export


def create_demo(bot=ConversationBot):
    sample_images = []
    all_imgs = [f"{SAMPLE_IMG_DIR}/{img}" for img in os.listdir(SAMPLE_IMG_DIR)]
    for i, img in enumerate(all_imgs):
        if i in [
            1,
            2,
            3,
        ]:
            sample_images.append(img)
    with gr.Blocks() as demo:
        gr_img = gr.Image(type="filepath")
        btn = gr.Button(value="Submit image")
        ingredients_msg = gr.Text(label="Ingredients from image")
        btn.click(bot.run_img, inputs=[gr_img], outputs=[ingredients_msg])
        gr.Examples(
            examples=sample_images,
            inputs=gr_img,
        )

        chatbot = gr.Chatbot(
            value=[(None, bot.ai_prompt_questions["ingredients"].prompt.template)]
        )

        msg = gr.Textbox()
        # clear = gr.Button("Clear")
        gr.Markdown("**🔃Refresh the page to start from scratch🔃**")

        msg.submit(
            fn=bot.respond, inputs=[msg, chatbot], outputs=[msg, chatbot], queue=False
        )
        # clear.click(lambda: None, None, chatbot, queue=False).then(bot.reset)
        return demo

In [ ]:
#| eval: false
if "demo" in globals():
    demo.close()
demo = create_demo(bot)
demo.launch()

Closing server running on port: 7860
Running on local URL:  http://127.0.0.1:7860

To create a public link, set `share=True` in `launch()`.


In [ ]:
#| hide
import nbdev

nbdev.nbdev_export()